In [1]:
# Set a working directory
#!pip install GitPython
import git
import os

repo = git.Repo('.', search_parent_directories=True)


os.chdir(repo.working_tree_dir)

In [2]:
# Running model preperation notebook that has a function we need to call
%run 'predictions/pred_functions.ipynb'


{4094}
<class 'list'>
<class 'list'>
[[ 3.45717163e+01  2.56531183e+01  5.76444444e-03 ...  9.46470396e+00
   1.95264180e+03  7.12944444e+00]
 [ 3.46093165e+01  2.56462433e+01 -2.25555556e-03 ...  9.46470396e+00
   1.95264180e+03  8.12972222e+00]
 [ 3.46269515e+01  2.52466600e+01 -1.54770833e-01 ...  9.54816445e+00
   1.95380275e+03  1.11466667e+01]
 ...
 [ 3.49623977e+01  2.48945779e+01 -4.86312500e-02 ...  5.54336847e-04
   1.95756288e+03  1.05333333e+01]
 [ 3.49623977e+01  2.48945779e+01 -4.86312500e-02 ...  6.59941725e-04
   1.95833642e+03  1.15255556e+01]
 [ 3.49402743e+01  2.50197858e+01 -5.21711111e-02 ...  6.59941725e-04
   1.95833642e+03  1.25227778e+01]]
Training Features Shape: (8, 4094, 11)
Training Labels Shape: (8, 4094)
Testing Features Shape: (8, 584, 11)
Testing Labels Shape: (8, 584)


In [3]:
import pandas as pd
global_df = pd.read_csv('data_ingest/data/modified/predictors_clean.csv')
global_df['biomass'] = 0.0
global_df['cruise'] = 'global'

In [4]:
global_pop_df, labels_global, features_global, feature_list_global = preprocess_single_population(global_df)

In [5]:
import joblib
from sklearn.ensemble import RandomForestRegressor
predictions = []
for f in fold:
    rf = joblib.load(f"RF_models/pro_random_forest_fold_{f}.joblib")
    
    # Use the model to predict on the test data for this fold
    preds = rf.predict(features_global)
    predictions.append(preds)

preds_global = pd.DataFrame(predictions).T


In [6]:
preds_global['mean'] = preds_global.mean(axis=1)

def pred_conf(preds):
    for i in range(len(preds)):
        preds['conf'] = preds.std(axis=1)
    return preds['conf']

preds_global['conf'] = pred_conf(preds_global[[0, 1, 2, 3, 4, 5, 6, 7]])

global_df['biomass'] = preds_global['mean']
global_df['std'] = preds_global['conf']
global_df['relative_std'] = (preds_global['conf'] / preds_global['mean'] * 100)

In [7]:
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px

fig = px.scatter_geo(global_df, lat='lat', lon='lon', hover_name='biomass', color='biomass')
fig.update_traces(marker=dict(size=3.5))
fig.update_layout(autosize=False,width = 1200, height = 700)
fig.show()

In [8]:
import plotly.express as px

fig = px.scatter_geo(global_df, lat='lat', lon='lon', hover_name='relative_std', color='relative_std')
fig.update_traces(marker=dict(size=3.5))
fig.update_layout(autosize=False,width = 1250, height = 750)
fig.show()